<img src="https://upload.wikimedia.org/wikipedia/commons/thumb/5/58/Uber_logo_2018.svg/1024px-Uber_logo_2018.svg.png" alt="UBER LOGO" width="50%" />

# UBER Pickups 

## Company's Description 📇

<a href="http://uber.com/" target="_blank">Uber</a> est l'une des startups les plus célèbres au monde. Elle a commencé comme une application de covoiturage pour les personnes qui ne pouvaient pas se permettre un taxi. Maintenant, Uber a étendu ses activités à la livraison de nourriture,  <a href="https://www.ubereats.com/fr-en" target="_blank">Uber Eats</a>, livraison de colis, au transport de marchandises et même au transport urbain avec <a href="https://www.uber.com/fr/en/ride/uber-bike/" target="_blank"> Jump Bike</a> and <a href="https://www.li.me/" target="_blank"> Lime </a> que l'entreprise a financés. 


L'objectif de l'entreprise est de révolutionner le transport à travers le monde. Elle opère désormais dans environ 70 pays et 900 villes, et génère un chiffre d'affaires de plus de 14 milliards de dollars ! 😮

## Projet 🚧

L'une des principales difficultés que l'équipe d'Uber a identifiées est que parfois, les conducteurs ne sont pas disponibles lorsque les utilisateurs en ont besoin. Par exemple, un utilisateur pourrait se trouver dans le quartier financier de San Francisco alors que les chauffeurs Uber recherchent des clients dans le quartier de Castro.

Même si les deux quartiers ne sont pas très éloignés, les utilisateurs doivent quand même attendre 10 à 15 minutes avant d'être pris en charge, ce qui est trop long. Les recherches d'Uber montrent que les utilisateurs acceptent d'attendre 5 à 7 minutes, sinon ils annuleront leur trajet.

Par conséquent, l'équipe de données d'Uber souhaite travailler sur un projet où leur application recommanderait des zones chaudes dans les grandes villes à tout moment de la journée.

## Objectifs 🎯

Uber dispose déjà de données sur les prises en charge dans les grandes villes. Votre objectif est de créer des algorithmes qui détermineront les zones chaudes où les conducteurs devraient se trouver. Par conséquent, vous allez :

* Créer un algorithme pour trouver les zones chaudes.
* Visualiser les résultats sur un tableau de bord attrayant.

## Scope du projet 🖼️

Pour commencer, Uber souhaite essayer cette fonctionnalité dans la ville de New York. Par conséquent, vous vous concentrerez uniquement sur cette ville. Les données peuvent être trouvées ici :

👉👉<a href="https://full-stack-bigdata-datasets.s3.eu-west-3.amazonaws.com/Machine+Learning+non+Supervis%C3%A9/Projects/uber-trip-data.zip" target="_blank"> Uber Trip Data</a> 👈👈

**Vous ne devez vous concentrer que sur la ville de New York pour ce projet.**

## Deliverable 📬

Pour mener à bien ce projet, votre équipe devrait :

* Avoir une carte avec des zones chaudes en utilisant n'importe quelle bibliothèque Python (plotly ou autre).
* Vous devriez au moins décrire les zones chaudes par jour de la semaine.
* Comparer les résultats avec au moins deux algorithmes non supervisés comme KMeans et DBScan.

Vos cartes devraient ressembler à quelque chose comme ceci :

<img src="https://full-stack-assets.s3.eu-west-3.amazonaws.com/images/Clusters_uber_pickups.png" alt="Uber Cluster Map" />

# Importation des librairies

In [2]:
import os
os.environ['OMP_NUM_THREADS'] = '1'

import warnings
warnings.filterwarnings('ignore', category=UserWarning, module='sklearn.cluster._kmeans')
warnings.filterwarnings('ignore', category=FutureWarning, module='sklearn.cluster._kmeans')

import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import numpy as np
import math
import matplotlib.pyplot as plt
import plotly.subplots as sp

from geopy.geocoders import Nominatim
from plotly.subplots import make_subplots
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from IPython.display import clear_output
from sklearn.cluster import DBSCAN
from sklearn.neighbors import NearestNeighbors


# EDA

### 1. Importation et analyse macro des différents dataframes

Tout d'abord, concaténons les df de courses de d'Avril à Septembre 2014 en un seul df pour avoir un seul df comportant toute les données disponibles de 2014 pour des analyse sommaires. Nous ferons de même avec le dataset des zones et de 2015 dans cette section.

In [2]:
# Concaténation des df de courses d'Avril à Septembre 2014 en un seul df.

csv_files = [
    'uber-trip-data/uber-raw-data-apr14.csv',
    'uber-trip-data/uber-raw-data-aug14.csv',
    'uber-trip-data/uber-raw-data-jul14.csv',
    'uber-trip-data/uber-raw-data-jun14.csv',
    'uber-trip-data/uber-raw-data-may14.csv',
    'uber-trip-data/uber-raw-data-sep14.csv'
]

dataframes = [pd.read_csv(f) for f in csv_files]

df_2014 = pd.concat(dataframes, ignore_index=True)
df_2014.head()

Date/Time      Lat      Lon    Base
0  4/1/2014 0:11:00  40.7690 -73.9549  B02512
1  4/1/2014 0:17:00  40.7267 -74.0345  B02512
2  4/1/2014 0:21:00  40.7316 -73.9873  B02512
3  4/1/2014 0:28:00  40.7588 -73.9776  B02512
4  4/1/2014 0:33:00  40.7594 -73.9722  B02512

In [3]:
#  Basiques stats df_2014
print("Number of rows : {}".format(df_2014.shape[0]))
print()

print("Display of dataset: ")
display(df_2014.head())
print()

print("Basics statistics: ")
data_desc_df_2014 = df_2014.describe(include='all')
display(data_desc_df_2014)
print()

print("Percentage of missing values: ")
display(100*df_2014.isnull().sum()/df_2014.shape[0])

Number of rows : 4534327

Display of dataset: 


Date/Time      Lat      Lon    Base
0  4/1/2014 0:11:00  40.7690 -73.9549  B02512
1  4/1/2014 0:17:00  40.7267 -74.0345  B02512
2  4/1/2014 0:21:00  40.7316 -73.9873  B02512
3  4/1/2014 0:28:00  40.7588 -73.9776  B02512
4  4/1/2014 0:33:00  40.7594 -73.9722  B02512


Basics statistics: 


Date/Time           Lat           Lon     Base
count             4534327  4.534327e+06  4.534327e+06  4534327
unique             260093           NaN           NaN        5
top     4/7/2014 20:21:00           NaN           NaN   B02617
freq                   97           NaN           NaN  1458853
mean                  NaN  4.073926e+01 -7.397302e+01      NaN
std                   NaN  3.994991e-02  5.726670e-02      NaN
min                   NaN  3.965690e+01 -7.492900e+01      NaN
25%                   NaN  4.072110e+01 -7.399650e+01      NaN
50%                   NaN  4.074220e+01 -7.398340e+01      NaN
75%                   NaN  4.076100e+01 -7.396530e+01      NaN
max                   NaN  4.211660e+01 -7.206660e+01      NaN


Percentage of missing values: 


Date/Time    0.0
Lat          0.0
Lon          0.0
Base         0.0
dtype: float64

In [4]:
# Import de df_zone qui couvre les zones géographiques des courses de taxis
df_zone = pd.read_csv("uber-trip-data/taxi-zone-lookup.csv")
df_zone.head()

LocationID        Borough                     Zone
0           1            EWR           Newark Airport
1           2         Queens              Jamaica Bay
2           3          Bronx  Allerton/Pelham Gardens
3           4      Manhattan            Alphabet City
4           5  Staten Island            Arden Heights

In [5]:
#  Basiques stats df_zone
print("Number of rows : {}".format(df_zone.shape[0]))
print()

print("Display of dataset: ")
display(df_zone.head())
print()

print("Basics statistics: ")
data_desc_zone = df_zone.describe(include='all')
display(data_desc_zone)
print()

print("Percentage of missing values: ")
display(100*df_zone.isnull().sum()/df_zone.shape[0])

Number of rows : 265

Display of dataset: 


LocationID        Borough                     Zone
0           1            EWR           Newark Airport
1           2         Queens              Jamaica Bay
2           3          Bronx  Allerton/Pelham Gardens
3           4      Manhattan            Alphabet City
4           5  Staten Island            Arden Heights


Basics statistics: 


LocationID Borough                                           Zone
count   265.000000     265                                            265
unique         NaN       7                                            261
top            NaN  Queens  Governor's Island/Ellis Island/Liberty Island
freq           NaN      69                                              3
mean    133.000000     NaN                                            NaN
std      76.643112     NaN                                            NaN
min       1.000000     NaN                                            NaN
25%      67.000000     NaN                                            NaN
50%     133.000000     NaN                                            NaN
75%     199.000000     NaN                                            NaN
max     265.000000     NaN                                            NaN


Percentage of missing values: 


LocationID    0.0
Borough       0.0
Zone          0.0
dtype: float64

In [6]:
# Import de df_2015 qui répertorie les courses de Janvier à juin 2015
df_2015= pd.read_csv("uber-trip-data/uber-raw-data-janjune-15.csv")
df_2015.head()

Dispatching_base_num          Pickup_date Affiliated_base_num  locationID
0               B02617  2015-05-17 09:47:00              B02617         141
1               B02617  2015-05-17 09:47:00              B02617          65
2               B02617  2015-05-17 09:47:00              B02617         100
3               B02617  2015-05-17 09:47:00              B02774          80
4               B02617  2015-05-17 09:47:00              B02617          90

In [7]:
#  Basiques stats df_2015
print("Number of rows : {}".format(df_zone.shape[0]))
print()

print("Display of dataset: ")
display(df_2015.head())
print()

print("Basics statistics: ")
data_desc_df_2015 = df_2015.describe(include='all')
display(data_desc_df_2015)
print()

print("Percentage of missing values: ")
display(100*df_2015.isnull().sum()/df_2015.shape[0])

Number of rows : 265

Display of dataset: 


Dispatching_base_num          Pickup_date Affiliated_base_num  locationID
0               B02617  2015-05-17 09:47:00              B02617         141
1               B02617  2015-05-17 09:47:00              B02617          65
2               B02617  2015-05-17 09:47:00              B02617         100
3               B02617  2015-05-17 09:47:00              B02774          80
4               B02617  2015-05-17 09:47:00              B02617          90


Basics statistics: 


Dispatching_base_num          Pickup_date Affiliated_base_num  \
count              14270479             14270479            14108284   
unique                    8              2744783                 284   
top                  B02764  2015-06-27 22:19:00              B02764   
freq                5753653                  213             4352321   
mean                    NaN                  NaN                 NaN   
std                     NaN                  NaN                 NaN   
min                     NaN                  NaN                 NaN   
25%                     NaN                  NaN                 NaN   
50%                     NaN                  NaN                 NaN   
75%                     NaN                  NaN                 NaN   
max                     NaN                  NaN                 NaN   

          locationID  
count   1.427048e+07  
unique           NaN  
top              NaN  
freq             NaN  
mean    1.520574e+02  
std     7.159620e+01  
min     1.000000e+00  
25%     9.200000e+01  
50%     1.570000e+02  
75%     2.300000e+02  
max     2.650000e+02


Percentage of missing values: 


Dispatching_base_num    0.000000
Pickup_date             0.000000
Affiliated_base_num     1.136577
locationID              0.000000
dtype: float64

Nous pouvons constater ici que les df n'ont pas de données manquantes significatives (seulement 1.13 pour la colonne Affiliated_base_num de df_2015 que nous n'utiliseront pas dans nos analyses futures)

Dans nos analyses, nous allons focaliser sur les dates, longitudes et latitudes pour comprendre les zones d'influence par jours et heures.

### 2. Focus df_2014 : Transformation et nettoyage.

Ce code prépare les données de trajets Uber de 2014 en supprimant la colonne 'Base', convertissant 'Date/Time' en format datetime, et créant de nouvelles colonnes pour le jour, le jour de la semaine et l'heure afin de réaliser nos analyses.

In [8]:
# Drop de la colonne Base
df_2014= df_2014.drop('Base', axis = 1)

In [9]:
# Conversion de la colonne 'Date/Time' au format datetime pour permettre le traitement temporel
df_2014['Date/Time'] = pd.to_datetime(df_2014['Date/Time'])

# Création de nouvelles colonnes temporelles
df_2014['day'] = df_2014['Date/Time'].dt.day
df_2014['dayofweek'] = df_2014['Date/Time'].dt.dayofweek
df_2014['hour'] = df_2014['Date/Time'].dt.hour

# Création d'une colonne 'Date/Hour' en arrondissant à l'heure la plus proche pour simplifier les différentes lectures.
df_2014['Date/Hour'] = df_2014['Date/Time'].dt.floor('H')

# Formatage des colonnes pour une visualisation plus facile.
df_2014['DayOfWeek'] = df_2014['Date/Hour'].dt.strftime('%A')  
df_2014['Hour'] = df_2014['Date/Hour'].dt.strftime('%H:%M:00')  
df_2014['DayOfWeek/Hour'] = df_2014['Date/Hour'].dt.strftime('%A-%H:%M:00')
df_2014['Date/Hour'] = df_2014['Date/Hour'].dt.strftime('%Y-%m-%d-%H:%M:00')  # Formatage complet avec date et heure

In [10]:
# Tri des valeurs pour les visualisations
df_2014 = df_2014.sort_values(['hour', 'dayofweek'], ascending=[True, True])

In [11]:
df_2014

Date/Time      Lat      Lon  day  dayofweek  hour  \
7785    2014-04-07 00:31:00  40.7205 -73.9939    7          0     0   
7786    2014-04-07 00:37:00  40.7407 -74.0077    7          0     0   
7787    2014-04-07 00:50:00  40.7591 -73.9892    7          0     0   
7788    2014-04-07 00:58:00  40.7419 -74.0034    7          0     0   
15857   2014-04-14 00:02:00  40.7456 -73.9773   14          0     0   
...                     ...      ...      ...  ...        ...   ...   
4520329 2014-09-28 23:57:00  40.6447 -73.7821   28          6    23   
4520330 2014-09-28 23:57:00  40.7513 -73.9941   28          6    23   
4520331 2014-09-28 23:57:00  40.6875 -74.1824   28          6    23   
4520332 2014-09-28 23:57:00  40.6482 -73.7823   28          6    23   
4520333 2014-09-28 23:59:00  40.6483 -73.7824   28          6    23   

                   Date/Hour DayOfWeek      Hour   DayOfWeek/Hour  
7785     2014-04-07-00:00:00    Monday  00:00:00  Monday-00:00:00  
7786     2014-04-07-00:00:00    Monday  00:00:00  Monday-00:00:00  
7787     2014-04-07-00:00:00    Monday  00:00:00  Monday-00:00:00  
7788     2014-04-07-00:00:00    Monday  00:00:00  Monday-00:00:00  
15857    2014-04-14-00:00:00    Monday  00:00:00  Monday-00:00:00  
...                      ...       ...       ...              ...  
4520329  2014-09-28-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
4520330  2014-09-28-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
4520331  2014-09-28-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
4520332  2014-09-28-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
4520333  2014-09-28-23:00:00    Sunday  23:00:00  Sunday-23:00:00  

[4534327 rows x 10 columns]

### 3. Transformation et nettoyage de df_zone

Cette étape utilise le géocodeur Nominatim pour obtenir les coordonnées géographiques des zones de New York. La fonction get_coordinates récupère la latitude et la longitude pour chaque zone, et les résultats sont ajoutés au DataFrame df_zone.

In [13]:
# Initialisation de geocoder
geolocator = Nominatim(user_agent="geoapiExercises")

# Fonction pour obtenir les coordonnées
def get_coordinates(zone):
    try:
        location = geolocator.geocode(zone + ", NY")
        return pd.Series([location.latitude, location.longitude])
    except:
        return pd.Series([None, None])

# Application de la fonction
df_zone[['Lat', 'Long']] = df_zone['Zone'].apply(get_coordinates)

In [14]:
#  Basiques stats df_zone
print("Number of rows : {}".format(df_zone.shape[0]))
print()

print("Display of dataset: ")
display(df_zone.head())
print()

print("Basics statistics: ")
data_desc_zone = df_zone.describe(include='all')
display(data_desc_zone)
print()

print("Percentage of missing values: ")
display(100*df_zone.isnull().sum()/df_zone.shape[0])

Number of rows : 265

Display of dataset: 


LocationID        Borough                     Zone        Lat       Long
0           1            EWR           Newark Airport        NaN        NaN
1           2         Queens              Jamaica Bay  40.603994 -73.835412
2           3          Bronx  Allerton/Pelham Gardens        NaN        NaN
3           4      Manhattan            Alphabet City  40.725102 -73.979583
4           5  Staten Island            Arden Heights  40.563700 -74.191603


Basics statistics: 


LocationID Borough                                           Zone  \
count   265.000000     265                                            265   
unique         NaN       7                                            261   
top            NaN  Queens  Governor's Island/Ellis Island/Liberty Island   
freq           NaN      69                                              3   
mean    133.000000     NaN                                            NaN   
std      76.643112     NaN                                            NaN   
min       1.000000     NaN                                            NaN   
25%      67.000000     NaN                                            NaN   
50%     133.000000     NaN                                            NaN   
75%     199.000000     NaN                                            NaN   
max     265.000000     NaN                                            NaN   

               Lat        Long  
count   196.000000  196.000000  
unique         NaN         NaN  
top            NaN         NaN  
freq           NaN         NaN  
mean     40.884429  -73.978022  
std       0.598082    0.530623  
min      40.541777  -78.369465  
25%      40.675873  -73.987647  
50%      40.734505  -73.919894  
75%      40.808378  -73.835968  
max      44.751610  -72.515328


Percentage of missing values: 


LocationID     0.000000
Borough        0.000000
Zone           0.000000
Lat           26.037736
Long          26.037736
dtype: float64

In [15]:
df_zone.drop(["Borough","Zone"],axis=1, inplace=True)

In [16]:
df_zone

LocationID        Lat       Long
0             1        NaN        NaN
1             2  40.603994 -73.835412
2             3        NaN        NaN
3             4  40.725102 -73.979583
4             5  40.563700 -74.191603
..          ...        ...        ...
260         261  40.711900 -74.012527
261         262  40.773514 -73.953631
262         263        NaN        NaN
263         264  42.613112 -73.806501
264         265  42.613112 -73.806501

[265 rows x 3 columns]

### 3. Transformation et nettoyage de df_2015

tout commme pour df_2014, ce code prépare les données de trajets Uber de 2015 en supprimant les colonnes 'Base'et convertit 'Pickup_date' en format datetime, et créant de nouvelles colonnes pour le jour, le jour de la semaine et l'heure afin de réaliser nos analyses.

In [17]:
# Drop des colonnes Base
df_2015= df_2015.drop(["Dispatching_base_num", "Affiliated_base_num"], axis = 1)

In [18]:
# Conversion de la colonne 'Date/Time' au format datetime pour permettre le traitement temporel
df_2015['Pickup_date'] = pd.to_datetime(df_2015['Pickup_date'])

# Création de nouvelles colonnes temporelles
df_2015['day'] = df_2015['Pickup_date'].dt.day
df_2015['dayofweek'] = df_2015['Pickup_date'].dt.dayofweek
df_2015['hour'] = df_2015['Pickup_date'].dt.hour

# Création d'une colonne 'Date/Hour' en arrondissant à l'heure la plus proche pour simplifier les différentes lectures.
df_2015['Date/Hour'] = df_2015['Pickup_date'].dt.floor('H')

# Formatage des colonnes pour une visualisation plus facile.
df_2015['DayOfWeek'] = df_2015['Date/Hour'].dt.strftime('%A')  
df_2015['Hour'] = df_2015['Date/Hour'].dt.strftime('%H:%M:00')  
df_2015['DayOfWeek/Hour'] = df_2015['Date/Hour'].dt.strftime('%A-%H:%M:00')
df_2015['Date/Hour'] = df_2015['Date/Hour'].dt.strftime('%Y-%m-%d-%H:%M:00')  # Formatage complet avec date et heure

In [19]:
# Tri des valeurs pour les visualisations
df_2015 = df_2015.sort_values(['hour', 'dayofweek'], ascending=[True, True])

In [20]:
df_2015

Pickup_date  locationID  day  dayofweek  hour  \
2350     2015-01-19 00:30:18         263   19          0     0   
2552     2015-01-19 00:20:18         141   19          0     0   
2594     2015-01-19 00:43:11         161   19          0     0   
2610     2015-01-19 00:14:26         132   19          0     0   
2611     2015-01-19 00:39:02         145   19          0     0   
...                      ...         ...  ...        ...   ...   
14239183 2015-01-04 23:21:53          48    4          6    23   
14239210 2015-01-04 23:39:48         225    4          6    23   
14239240 2015-01-04 23:06:12         230    4          6    23   
14239241 2015-01-04 23:21:42         234    4          6    23   
14239247 2015-01-04 23:33:35         113    4          6    23   

                    Date/Hour DayOfWeek      Hour   DayOfWeek/Hour  
2350      2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00  
2552      2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00  
2594      2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00  
2610      2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00  
2611      2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00  
...                       ...       ...       ...              ...  
14239183  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
14239210  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
14239240  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
14239241  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
14239247  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  

[14270479 rows x 9 columns]

### 4. Fusions des dataframes

Nous fusionnons l'ensemble des dfs par jointure afin de former final_df et nous nettoyons les NaN des colonnes Lag et Lon.

In [21]:
# Jointure entre df_2015 et df_zone
df_2015.rename(columns={'locationID': 'LocationID'}, inplace=True)

df_2015_enriched = df_2015.merge(df_zone, on='LocationID', how='left')

In [22]:
df_2015_enriched

Pickup_date  LocationID  day  dayofweek  hour  \
0        2015-01-19 00:30:18         263   19          0     0   
1        2015-01-19 00:20:18         141   19          0     0   
2        2015-01-19 00:43:11         161   19          0     0   
3        2015-01-19 00:14:26         132   19          0     0   
4        2015-01-19 00:39:02         145   19          0     0   
...                      ...         ...  ...        ...   ...   
14270474 2015-01-04 23:21:53          48    4          6    23   
14270475 2015-01-04 23:39:48         225    4          6    23   
14270476 2015-01-04 23:06:12         230    4          6    23   
14270477 2015-01-04 23:21:42         234    4          6    23   
14270478 2015-01-04 23:33:35         113    4          6    23   

                    Date/Hour DayOfWeek      Hour   DayOfWeek/Hour        Lat  \
0         2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00        NaN   
1         2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00        NaN   
2         2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00  41.927015   
3         2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00  40.642948   
4         2015-01-19-00:00:00    Monday  00:00:00  Monday-00:00:00  40.741509   
...                       ...       ...       ...              ...        ...   
14270474  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  41.030914   
14270475  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  42.387863   
14270476  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  40.759508   
14270477  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  40.736072   
14270478  2015-01-04-23:00:00    Sunday  23:00:00  Sunday-23:00:00  43.037195   

               Long  
0               NaN  
1               NaN  
2        -73.999064  
3        -73.779373  
4        -73.956975  
...             ...  
14270474 -73.865282  
14270475 -73.775751  
14270476 -73.984159  
14270477 -73.990189  
14270478 -73.377830  

[14270479 rows x 11 columns]

In [23]:
# Jointure entre df_2014 et df_2015_enriched
df_2014.rename(columns={'Date/Time': 'Pickup_date', 'Lon': 'Long'})


final_df = pd.concat([df_2014, df_2015_enriched], ignore_index=True)

In [24]:
# Unification des clones 'Date/Time' et 'Pickup_date' en une seule colonne 'Unified_DateTime'
final_df['Unified_DateTime'] = final_df['Date/Time'].fillna(final_df['Pickup_date'])

# Convertit cette nouvelle colonne en type datetime
final_df['Unified_DateTime'] = pd.to_datetime(final_df['Unified_DateTime'])

# Drop de 'Date/Time' et 'Pickup_date après unification
final_df.drop(["Pickup_date", 'Date/Time'], axis= 1 ,inplace=True)

In [25]:
final_df

Lat      Lon  day  dayofweek  hour            Date/Hour  \
0         40.720500 -73.9939    7          0     0  2014-04-07-00:00:00   
1         40.740700 -74.0077    7          0     0  2014-04-07-00:00:00   
2         40.759100 -73.9892    7          0     0  2014-04-07-00:00:00   
3         40.741900 -74.0034    7          0     0  2014-04-07-00:00:00   
4         40.745600 -73.9773   14          0     0  2014-04-14-00:00:00   
...             ...      ...  ...        ...   ...                  ...   
18804801  41.030914      NaN    4          6    23  2015-01-04-23:00:00   
18804802  42.387863      NaN    4          6    23  2015-01-04-23:00:00   
18804803  40.759508      NaN    4          6    23  2015-01-04-23:00:00   
18804804  40.736072      NaN    4          6    23  2015-01-04-23:00:00   
18804805  43.037195      NaN    4          6    23  2015-01-04-23:00:00   

         DayOfWeek      Hour   DayOfWeek/Hour  LocationID       Long  \
0           Monday  00:00:00  Monday-00:00:00         NaN        NaN   
1           Monday  00:00:00  Monday-00:00:00         NaN        NaN   
2           Monday  00:00:00  Monday-00:00:00         NaN        NaN   
3           Monday  00:00:00  Monday-00:00:00         NaN        NaN   
4           Monday  00:00:00  Monday-00:00:00         NaN        NaN   
...            ...       ...              ...         ...        ...   
18804801    Sunday  23:00:00  Sunday-23:00:00        48.0 -73.865282   
18804802    Sunday  23:00:00  Sunday-23:00:00       225.0 -73.775751   
18804803    Sunday  23:00:00  Sunday-23:00:00       230.0 -73.984159   
18804804    Sunday  23:00:00  Sunday-23:00:00       234.0 -73.990189   
18804805    Sunday  23:00:00  Sunday-23:00:00       113.0 -73.377830   

            Unified_DateTime  
0        2014-04-07 00:31:00  
1        2014-04-07 00:37:00  
2        2014-04-07 00:50:00  
3        2014-04-07 00:58:00  
4        2014-04-14 00:02:00  
...                      ...  
18804801 2015-01-04 23:21:53  
18804802 2015-01-04 23:39:48  
18804803 2015-01-04 23:06:12  
18804804 2015-01-04 23:21:42  
18804805 2015-01-04 23:33:35  

[18804806 rows x 12 columns]

In [26]:
# Réordonne les colonnes du DataFrame

columns_order = [
    'LocationID', 'Unified_DateTime', 'DayOfWeek', 'Hour', 'DayOfWeek/Hour', 
    'Lat', 'Long'
]

final_df = final_df[columns_order]

final_df.head()

LocationID    Unified_DateTime DayOfWeek      Hour   DayOfWeek/Hour  \
0         NaN 2014-04-07 00:31:00    Monday  00:00:00  Monday-00:00:00   
1         NaN 2014-04-07 00:37:00    Monday  00:00:00  Monday-00:00:00   
2         NaN 2014-04-07 00:50:00    Monday  00:00:00  Monday-00:00:00   
3         NaN 2014-04-07 00:58:00    Monday  00:00:00  Monday-00:00:00   
4         NaN 2014-04-14 00:02:00    Monday  00:00:00  Monday-00:00:00   

       Lat  Long  
0  40.7205   NaN  
1  40.7407   NaN  
2  40.7591   NaN  
3  40.7419   NaN  
4  40.7456   NaN

In [27]:
#  Basiques stats final_df
print("Number of rows : {}".format(df_zone.shape[0]))
print()

print("Display of dataset: ")
display(df_zone.head())
print()

print("Basics statistics: ")
data_desc_zone = df_zone.describe(include='all')
display(data_desc_zone)
print()

print("Percentage of missing values: ")
display(100*df_zone.isnull().sum()/df_zone.shape[0])

Number of rows : 265

Display of dataset: 


LocationID        Lat       Long
0           1        NaN        NaN
1           2  40.603994 -73.835412
2           3        NaN        NaN
3           4  40.725102 -73.979583
4           5  40.563700 -74.191603


Basics statistics: 


LocationID         Lat        Long
count  265.000000  196.000000  196.000000
mean   133.000000   40.884429  -73.978022
std     76.643112    0.598082    0.530623
min      1.000000   40.541777  -78.369465
25%     67.000000   40.675873  -73.987647
50%    133.000000   40.734505  -73.919894
75%    199.000000   40.808378  -73.835968
max    265.000000   44.751610  -72.515328


Percentage of missing values: 


LocationID     0.000000
Lat           26.037736
Long          26.037736
dtype: float64

In [28]:
# Suppresion des lignes où les valeurs de 'Lat' ou 'Long' sont NaN
final_df = final_df.dropna(subset=['Lat', 'Long'])

final_df

LocationID    Unified_DateTime DayOfWeek      Hour   DayOfWeek/Hour  \
4534329        161.0 2015-01-19 00:43:11    Monday  00:00:00  Monday-00:00:00   
4534330        132.0 2015-01-19 00:14:26    Monday  00:00:00  Monday-00:00:00   
4534331        145.0 2015-01-19 00:39:02    Monday  00:00:00  Monday-00:00:00   
4534333        164.0 2015-01-19 00:27:54    Monday  00:00:00  Monday-00:00:00   
4534334        257.0 2015-01-19 00:14:42    Monday  00:00:00  Monday-00:00:00   
...              ...                 ...       ...       ...              ...   
18804801        48.0 2015-01-04 23:21:53    Sunday  23:00:00  Sunday-23:00:00   
18804802       225.0 2015-01-04 23:39:48    Sunday  23:00:00  Sunday-23:00:00   
18804803       230.0 2015-01-04 23:06:12    Sunday  23:00:00  Sunday-23:00:00   
18804804       234.0 2015-01-04 23:21:42    Sunday  23:00:00  Sunday-23:00:00   
18804805       113.0 2015-01-04 23:33:35    Sunday  23:00:00  Sunday-23:00:00   

                Lat       Long  
4534329   41.927015 -73.999064  
4534330   40.642948 -73.779373  
4534331   40.741509 -73.956975  
4534333   40.749842 -73.984251  
4534334   40.653487 -73.977196  
...             ...        ...  
18804801  41.030914 -73.865282  
18804802  42.387863 -73.775751  
18804803  40.759508 -73.984159  
18804804  40.736072 -73.990189  
18804805  43.037195 -73.377830  

[9956153 rows x 7 columns]

#### 5. Exploration de final_DF

Pour ce projet, il est important de comprendre où et quand les demandes de courses se concentrent le plus.
C'est pourquoi, nous analyserons les tendances globales du nombre de courses demandées par les clients au fil du temps afin d'avoir une meilleur compréhension afin d'avoir une meilleure compréhension des périodes les plus actives et de mieux cibler les efforts de déploiement des chauffeurs. 
Cette analyse nous permettra également de choisir les intervalles temporels les plus pertinents pour observer les variations de la demande.

In [30]:
# Extrait le jour de la semaine
final_df['DayOfWeek'] = final_df['Unified_DateTime'].dt.day_name()

# Crée un subplot avec 3 lignes et 3 colonnes.
fig = make_subplots(rows=3, cols=3, specs=[[{"colspan": 1}, {"colspan": 1}, {"colspan": 1}],
                                             [{"colspan": 1}, {"colspan": 1}, {"colspan": 1}],
                                             [{"colspan": 3}, None, None]],
                    subplot_titles=('Lundi', 'Mardi', 'Mercredi', 'Jeudi', 'Vendredi', 'Samedi', 'Dimanche'))

# Jours de la semaine en ordre
days_of_week = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']

# Coordonnées de positionnement des graphiques dans le subplot
positions = [(1, 1), (1, 2), (1, 3), 
             (2, 1), (2, 2), (2, 3), 
             (3, 1)]

# Boucle pour créer un histogramme pour chaque jour, avec positionnement spécifique
for (day, pos) in zip(days_of_week, positions):
    # Filtrer les données pour le jour spécifique
    day_data = final_df[final_df['DayOfWeek'] == day]
    
    # Crée l'histogramme pour ce jour
    hist = px.histogram(day_data, x='Unified_DateTime', nbins=len(day_data['Unified_DateTime'].dt.date.unique()))
    
    # Ajoute l'histogramme au subplot correspondant
    for trace in hist.data:
        fig.add_trace(trace, row=pos[0], col=pos[1])

# Mise à jour des axes et de la mise en page
fig.update_layout(height=1200, width=1200, title_text="Distribution des demandes Uber par jour de la semaine",
                  showlegend=False)
fig.update_xaxes(tickangle=-45, tickformat='%d-%m')

fig.show()

In [31]:
# Assure qu'Unified_DateTime' est au format datetime
final_df['Unified_DateTime'] = pd.to_datetime(final_df['Unified_DateTime'])

# Extrait le jour de la semaine et l'heure
final_df['DayOfWeek'] = final_df['Unified_DateTime'].dt.day_name()
final_df['Hour'] = final_df['Unified_DateTime'].dt.hour

# Crée un subplot avec 3 lignes et 3 colonnes
fig = make_subplots(rows=3, cols=3, specs=[[{"colspan": 1}, {"colspan": 1}, {"colspan": 1}],
                                             [{"colspan": 1}, {"colspan": 1}, {"colspan": 1}],
                                             [{"colspan": 3}, None, None]],
                    subplot_titles=('Lundi', 'Mardi', 'Mercredi', 'Jeudi', 'Vendredi', 'Samedi', 'Dimanche'))

# Jours de la semaine en ordre
days_of_week = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']

# Coordonnées de positionnement des graphiques dans le subplot
positions = [(1, 1), (1, 2), (1, 3), 
             (2, 1), (2, 2), (2, 3), 
             (3, 1)]

# Boucle pour créer un histogramme pour chaque jour, par heure
for (day, pos) in zip(days_of_week, positions):
    # Filtrer les données pour le jour spécifique
    day_data = final_df[final_df['DayOfWeek'] == day]
    
    # Crée l'histogramme pour chaque heure de ce jour
    hist = px.histogram(day_data, x='Hour', nbins=24)  # 24 heures dans une journée
    
    # Ajoute l'histogramme au subplot correspondant
    for trace in hist.data:
        fig.add_trace(trace, row=pos[0], col=pos[1])

# Mise à jour des axes et de la mise en page
fig.update_layout(height=1200, width=1200, title_text="Distribution horaire des demandes Uber par jour de la semaine",
                  showlegend=False)
fig.update_xaxes(tickmode='linear', tick0=0, dtick=1)  # Assure que toutes les heures sont affichées

fig.show()

Les graphiques montrent une variabilité notable de la demande Uber entre les jours de semaine et les week-ends, avec des pics d'activité plus marqués les samedis, suggérant une augmentation des sorties sociales et de loisirs. 

Les jours de semaine affichent une demande plus régulière, possiblement influencée par les trajets domicile-travail, avec une montée graduelle des demandes au cours de la journée et un pic en fin de journée.

A noter que les observations peuvent-être influencées par des facteurs locaux tels que des événements spécifiques, la météo, et les vacances, affectant les habitudes de mobilité des utilisateurs.

#### 6. Preprocessing


Par soucis de computation, nous nous concentrerons sur les datas structurées de septembre 2014 en guise d'échantillon pour la réalisation des préprocessing et création de modèles plutôt que sur final_df beaucoup trop consistant pour tout charger. 

En effet, df_final me provoque systèmatiquement un MemoryError ou un arrêt de mon kernel, toutefois, nous avons pu constater la méthodologie pour concaténer l'ensemble du df afin de réaliser des analyses sur l'entièreté des données si votre machine le permet. (Il suffit de changer le nom du df lors des étapes suivantes)

In [3]:
# Df sélectionné pour le modele suite à des soucis de MemoryError
df_model = pd.read_csv('uber-trip-data/uber-raw-data-sep14.csv')
df_model

Date/Time      Lat      Lon    Base
0          9/1/2014 0:01:00  40.2201 -74.0021  B02512
1          9/1/2014 0:01:00  40.7500 -74.0027  B02512
2          9/1/2014 0:03:00  40.7559 -73.9864  B02512
3          9/1/2014 0:06:00  40.7450 -73.9889  B02512
4          9/1/2014 0:11:00  40.8145 -73.9444  B02512
...                     ...      ...      ...     ...
1028131  9/30/2014 22:57:00  40.7668 -73.9845  B02764
1028132  9/30/2014 22:57:00  40.6911 -74.1773  B02764
1028133  9/30/2014 22:58:00  40.8519 -73.9319  B02764
1028134  9/30/2014 22:58:00  40.7081 -74.0066  B02764
1028135  9/30/2014 22:58:00  40.7140 -73.9496  B02764

[1028136 rows x 4 columns]

In [4]:
# Echantillon de données pour un calcul rapide des données
SAMPLE_SIZE = 30000
df_model = df_model.drop('Base', axis = 1)
df_model = df_model.sample(SAMPLE_SIZE, random_state = 0) 

##### 6.1 Préprocessing des dates

Suite à la selection de df_model, nous devons réaliser les transformations des dates à nouveaux (non nécessaire pour final_df).

In [5]:
# Traitements des datetime
df_model['Date/Time'] = pd.to_datetime(df_model['Date/Time'])
df_model['day'] = df_model['Date/Time'].dt.day
df_model['dayofweek'] = df_model['Date/Time'].dt.dayofweek
df_model['hour'] = df_model['Date/Time'].dt.hour
df_model['Date/Hour'] = df_model['Date/Time'].dt.floor('H') # Supprimer les minutes/secondes/niveau de précision
df_model['DayOfWeek'] = df_model['Date/Hour'].dt.strftime('%A')

# Convertit les horodatages en chaînes de caractères pour pouvoir les utiliser comme étiquettes dans les figures
df_model['Hour'] = df_model['Date/Hour'].dt.strftime('%H:%M:00')
df_model['DayOfWeek/Hour'] = df_model['Date/Hour'].dt.strftime('%A-%H:%M:00') 
df_model['Date/Hour'] = df_model['Date/Hour'].dt.strftime('%Y-%m-%d-%H:%M:00')

# Ordonne les valeurs pour correspondre à l'ordre de bouclage pour les visualisations
df_model = df_model.sort_values(['hour','dayofweek'], ascending=[True,True]) 

df_model


Date/Time      Lat      Lon  day  dayofweek  hour  \
14     2014-09-01 00:48:00  40.7378 -74.0395    1          0     0   
150425 2014-09-15 00:18:00  40.7325 -73.9991   15          0     0   
631274 2014-09-29 00:13:00  40.7500 -73.9980   29          0     0   
366563 2014-09-08 00:55:00  40.7523 -73.9744    8          0     0   
34385  2014-09-01 00:05:00  40.7257 -73.9900    1          0     0   
...                    ...      ...      ...  ...        ...   ...   
261002 2014-09-28 23:46:00  40.6448 -73.7821   28          6    23   
917663 2014-09-14 23:36:00  40.7557 -73.9835   14          6    23   
208969 2014-09-21 23:03:00  40.6448 -73.7819   21          6    23   
366396 2014-09-07 23:42:00  40.6486 -73.7829    7          6    23   
459342 2014-09-14 23:46:00  40.7667 -73.9848   14          6    23   

                  Date/Hour DayOfWeek      Hour   DayOfWeek/Hour  
14      2014-09-01-00:00:00    Monday  00:00:00  Monday-00:00:00  
150425  2014-09-15-00:00:00    Monday  00:00:00  Monday-00:00:00  
631274  2014-09-29-00:00:00    Monday  00:00:00  Monday-00:00:00  
366563  2014-09-08-00:00:00    Monday  00:00:00  Monday-00:00:00  
34385   2014-09-01-00:00:00    Monday  00:00:00  Monday-00:00:00  
...                     ...       ...       ...              ...  
261002  2014-09-28-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
917663  2014-09-14-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
208969  2014-09-21-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
366396  2014-09-07-23:00:00    Sunday  23:00:00  Sunday-23:00:00  
459342  2014-09-14-23:00:00    Sunday  23:00:00  Sunday-23:00:00  

[30000 rows x 10 columns]

In [6]:
# Colonnes conservées pour les entrainements des modèles
columns_to_keep = ['Lat', 'Lon', 'DayOfWeek/Hour']
df_model = df_model[columns_to_keep]
df_model

Lat      Lon   DayOfWeek/Hour
14      40.7378 -74.0395  Monday-00:00:00
150425  40.7325 -73.9991  Monday-00:00:00
631274  40.7500 -73.9980  Monday-00:00:00
366563  40.7523 -73.9744  Monday-00:00:00
34385   40.7257 -73.9900  Monday-00:00:00
...         ...      ...              ...
261002  40.6448 -73.7821  Sunday-23:00:00
917663  40.7557 -73.9835  Sunday-23:00:00
208969  40.6448 -73.7819  Sunday-23:00:00
366396  40.6486 -73.7829  Sunday-23:00:00
459342  40.7667 -73.9848  Sunday-23:00:00

[30000 rows x 3 columns]

##### 6.1 Préprocessing des distances

Dans notre approche pour entraîner un modèle de DBSCAN, nous allons inclure l'utilisation de GridSearch pour optimiser le paramètre eps, garantissant ainsi des clusters de haute qualité.

Nous commencerons par prétraiter les données en convertissant les coordonnées géographiques en coordonnées cartésiennes 3D, ce qui simplifie le calcul des distances. Ces coordonnées cartésiennes seront ensuite utilisées comme caractéristiques pour le clustering.

Pour définir les paramètres de DBSCAN, nous fixons min_samples à 3% de la demande moyenne par plage horaire, garantissant que les clusters sont significatifs. En analysant les données, nous avons constaté que la demande peut varier considérablement entre différentes plages horaires. En fixant min_samples à 3% de la demande moyenne, nous nous assurons que chaque cluster identifié représente une proportion non négligeable de la demande totale, ce qui signifie qu'il y a suffisamment de points pour former un cluster dense et pertinent.

Nous effectuerons ensuite une recherche en grille sur une plage de valeurs pour eps (de 0.1 à 1.0) afin de trouver la meilleure valeur qui maximise le score de silhouette. Pour chaque plage horaire, nous trouverons le meilleur eps.

Enfin, nous résumerons les données en calculant la demande pour chaque cluster et le pourcentage de la demande totale qu'il représente, nous permettant ainsi d'obtenir une vue d'ensemble des zones de forte demande et d'optimiser la répartition des chauffeurs.

In [7]:
# Convertit la latitude et la longitude en coordonnées cartésiennes 3D.
def lat_lon_to_cartesian(lat, lon, R=6371):
    
    # Convertit les degrés en radians
    lat, lon = np.radians(lat), np.radians(lon)  # lat (float) : Latitude en degrés et lon (float) : Longitude en degrés.
    
    # Calcule les coordonnées cartésiennes
    x = R * np.cos(lat) * np.cos(lon)  # R (int) : Rayon de la Terre en kilomètres. La valeur par défaut est 6371 km.
    y = R * np.cos(lat) * np.sin(lon)  # tuple : Tuple contenant les coordonnées cartésiennes x, y.
    
    return x, y


In [8]:
# Applique la fonction pour convertir les coordonnées géographiques en coordonnées cartésiennes
df_model[['x', 'y']] = df_model.apply(lambda row: lat_lon_to_cartesian(row['Lat'], row['Lon']), axis=1, result_type='expand')
clustering_features = ['x','y']

df_model

C:\Users\33671\AppData\Local\Temp\ipykernel_10372\3522838456.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_model[['x', 'y']] = df_model.apply(lambda row: lat_lon_to_cartesian(row['Lat'], row['Lon']), axis=1, result_type='expand')
C:\Users\33671\AppData\Local\Temp\ipykernel_10372\3522838456.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_model[['x', 'y']] = df_model.apply(lambda row: lat_lon_to_cartesian(row['Lat'], row['Lon']), axis=1, result_type='expand')


Lat      Lon   DayOfWeek/Hour            x            y
14      40.7378 -74.0395  Monday-00:00:00  1327.393625 -4641.245488
150425  40.7325 -73.9991  Monday-00:00:00  1330.771907 -4640.678050
631274  40.7500 -73.9980  Monday-00:00:00  1330.510903 -4639.431722
366563  40.7523 -73.9744  Monday-00:00:00  1332.375673 -4638.722836
34385   40.7257 -73.9900  Monday-00:00:00  1331.645017 -4640.940855
...         ...      ...              ...          ...          ...
261002  40.6448 -73.7821  Sunday-23:00:00  1350.113899 -4641.709331
917663  40.7557 -73.9835  Sunday-23:00:00  1331.570815 -4638.697168
208969  40.6448 -73.7819  Sunday-23:00:00  1350.130102 -4641.704619
366396  40.6486 -73.7829  Sunday-23:00:00  1349.972220 -4641.463894
459342  40.7667 -73.9848  Sunday-23:00:00  1331.245238 -4637.959774

[30000 rows x 5 columns]

##### 6.3 Division des données selon les plages horaires

Division des données par plages horaires : un clustering indépendant sera effectué pour chaque plage horaire afin de déterminer les influences par heures sur chaque jour.

In [9]:
# Division des données par plages horaires
timeframes = df_model['DayOfWeek/Hour'].unique()
timeframe_data_list = []
for timeframe in timeframes:
    timeframe_data_list.append(df_model[df_model['DayOfWeek/Hour'] == timeframe])
print("Numbre de timeframes: ", len(timeframe_data_list))

timeframe_data_list[:3]

Numbre de timeframes:  168


[             Lat      Lon   DayOfWeek/Hour            x            y
 14       40.7378 -74.0395  Monday-00:00:00  1327.393625 -4641.245488
 150425   40.7325 -73.9991  Monday-00:00:00  1330.771907 -4640.678050
 631274   40.7500 -73.9980  Monday-00:00:00  1330.510903 -4639.431722
 366563   40.7523 -73.9744  Monday-00:00:00  1332.375673 -4638.722836
 34385    40.7257 -73.9900  Monday-00:00:00  1331.645017 -4640.940855
 699011   40.7234 -73.9999  Monday-00:00:00  1330.889092 -4641.331270
 209143   40.7644 -73.9883  Monday-00:00:00  1331.007981 -4638.201602
 275048   40.6886 -73.9559  Monday-00:00:00  1335.150467 -4642.733210
 275254   40.7173 -74.0018  Monday-00:00:00  1330.857134 -4641.800758
 275002   40.7034 -73.9908  Monday-00:00:00  1332.026297 -4642.514170
 652678   40.8060 -73.9654  Monday-00:00:00  1332.027045 -4634.765182
 34465    40.7254 -73.9849  Monday-00:00:00  1332.064115 -4640.843224
 631341   40.7767 -73.9556  Monday-00:00:00  1333.408041 -4636.582851
 34409    40.7255 -7

### 7. Entrainement des modèles de clustering: Kmeans et DBSCAN


#### 7.1 Kmeans (WCSS et Silhouette)

Lorsque nous exécutons un algorithme KMeans, le paramètre crucial à déterminer est le nombre de clusters, noté 'k'. Cependant, trouver la valeur optimale de 'k' peut être complexe et peut varier selon les plages horaires.

Pour résoudre ce défi, nous adoptons une approche systématique : pour chaque plage horaire, nous lançons 9 algorithmes KMeans avec des valeurs de 'k' allant de 2 à 10. Ensuite, nous évaluons chaque modèle en calculant à la fois le score de silhouette et l'inertie WCSS.

* L'inertie WCSS mesure la compacité des clusters : plus elle est faible, plus les points d'un même cluster sont proches les uns des autres.
* Le score de silhouette mesure à quel point les clusters sont bien séparés : un score plus élevé indique une meilleure séparation entre les clusters.

Pour choisir le meilleur 'k', nous comparons ces deux métriques en les mettant à l'échelle pour qu'elles soient comparables. Nous calculons alors un score comme la différence entre le score de silhouette mis à l'échelle et l'inertie WCSS mise à l'échelle, et sélectionnons 'k' pour chaque plage horaire qui maximise ce score.

In [10]:
# Identifie pour chaque plage horaire le meilleur nombre de clusters à utiliser

# Configuration initiale et définition des paramètres
print(f"Recherche du paramètre k optimal pour chacune des {len(timeframe_data_list)} plages horaires :")

timeframes_nb = len(timeframe_data_list)
optimum_k_list = []
sc = StandardScaler()

# Boucle principale pour trouver le nombre optimal de clusters pour chaque plage horaire
for i in range(timeframes_nb):
    wcss_list = []
    sil_list = []
    k_list = []
    
    for k in range(2, 11): 
        X = timeframe_data_list[i][clustering_features]
        kmeans = KMeans(n_clusters=k, random_state=0, n_init='auto')
        kmeans.fit(X)
        wcss_list.append(kmeans.inertia_)
        sil_list.append(silhouette_score(X, kmeans.predict(X)))
        k_list.append(k)
        
    k_choice = pd.DataFrame({'k': k_list, 'WCSS': wcss_list, 'Silhouette Score': sil_list}).set_index('k')
    k_choice_scaled = sc.fit_transform(k_choice)
    k_choice['score'] = k_choice_scaled[:, 1] - k_choice_scaled[:, 0]
    optimum_k = k_choice.index[k_choice['score'].argmax()]
    optimum_k_list.append(optimum_k)

print("Terminé!")

Recherche du paramètre k optimal pour chacune des 168 plages horaires :
Terminé!


In [11]:
# Exécute le KMeans optimisé sur chaque plage horaire

print(f"Entraînement d'un KMeans sur chacune des {len(timeframe_data_list)} plages horaires :")

for i in range(timeframes_nb):
    kmeans = KMeans(n_clusters = optimum_k_list[i], random_state = 0)
    kmeans.fit(timeframe_data_list[i][clustering_features])
    timeframe_data_list[i]['cluster'] = kmeans.labels_
    timeframe_data_list[i] = timeframe_data_list[i].sort_values('cluster')
print("Terminé !")

Entraînement d'un KMeans sur chacune des 168 plages horaires :


C:\Users\33671\AppData\Local\Temp\ipykernel_10372\1649788717.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = kmeans.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_10372\1649788717.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = kmeans.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_10372\1649788717.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexe

Terminé !


C:\Users\33671\AppData\Local\Temp\ipykernel_10372\1649788717.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = kmeans.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_10372\1649788717.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = kmeans.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_10372\1649788717.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexe

#### 7.2 Visualisation graphiques des clusters Kmeans

Commençons tout d'abord par afficher un graphe pour un timframe particulier

In [12]:
timeframe_summary_list = []

for timeframe_data in timeframe_data_list:

    # Crée un dataframe résumant le nombre de demandes de prise en charge pour chaque cluster dans la plage horaire, et le % de la demande de la plage horaire qu'il représente :
    timeframe_demand = len(timeframe_data)
    clusters_size = timeframe_data.groupby(['DayOfWeek/Hour', 'cluster']).count()['Lat'].rename('count').reset_index(drop = False)
    clusters_size['%_of_timeframe_demand'] = (clusters_size['count'] / timeframe_demand * 100).astype(int)
    
    # Fusionne les informations dans chaque plage horaire :
    timeframe_summary = timeframe_data.merge(clusters_size, on = ['DayOfWeek/Hour', 'cluster'])
    
    # Crée une colonne avec le texte à afficher pour chaque cluster dans la plage horaire :
    timeframe_summary['cluster / % of demand'] = '#' + timeframe_summary['cluster'].astype(str) + ' / ' + timeframe_summary['%_of_timeframe_demand'].astype(str) + '%'
    
    # Sépare l'identification de la plage horaire en deux (jour de la semaine, heure) pour surveiller l'un dans les sous-graphiques et l'autre dans le curseur de la figure plotly
    timeframe_summary['DayOfWeek'] = timeframe_summary['DayOfWeek/Hour'].str.partition('-')[0]
    timeframe_summary['Hour'] = timeframe_summary['DayOfWeek/Hour'].str.partition('-')[2]
    
    timeframe_summary_list.append(timeframe_summary)

In [13]:
print("Exemple pour un timeframe :")
timeframe_example = timeframe_summary_list[50]
display(timeframe_example)
fig = px.scatter_mapbox(timeframe_example, lat = 'Lat', lon = 'Lon', 
                      mapbox_style="carto-positron", 
                      color = timeframe_example['cluster / % of demand'].astype(str), 
                      height = 700, zoom = 10
                     )
fig.show()

Exemple pour un timeframe :


Lat      Lon    DayOfWeek/Hour            x            y  cluster  \
0    40.7606 -73.9947  Tuesday-07:00:00  1330.565950 -4638.615442        0   
1    40.7284 -74.0036  Tuesday-07:00:00  1330.489402 -4641.068510        0   
2    40.7304 -73.9822  Tuesday-07:00:00  1332.182711 -4640.431775        0   
3    40.7362 -73.9843  Tuesday-07:00:00  1331.896518 -4640.076092        0   
4    40.7303 -74.0080  Tuesday-07:00:00  1330.095012 -4641.038155        0   
..       ...      ...               ...          ...          ...      ...   
273  40.6771 -74.0066  Tuesday-07:00:00  1331.271346 -4644.714153        5   
274  40.6831 -73.9513  Tuesday-07:00:00  1335.633425 -4643.009155        5   
275  40.7022 -73.9828  Tuesday-07:00:00  1332.698511 -4642.411778        5   
276  40.5926 -73.9415  Tuesday-07:00:00  1338.240481 -4649.078781        5   
277  41.0528 -74.0323  Tuesday-07:00:00  1321.668634 -4619.032381        6   

     count  %_of_timeframe_demand cluster / % of demand DayOfWeek      Hour  
0      137                     49              #0 / 49%   Tuesday  07:00:00  
1      137                     49              #0 / 49%   Tuesday  07:00:00  
2      137                     49              #0 / 49%   Tuesday  07:00:00  
3      137                     49              #0 / 49%   Tuesday  07:00:00  
4      137                     49              #0 / 49%   Tuesday  07:00:00  
..     ...                    ...                   ...       ...       ...  
273     25                      8               #5 / 8%   Tuesday  07:00:00  
274     25                      8               #5 / 8%   Tuesday  07:00:00  
275     25                      8               #5 / 8%   Tuesday  07:00:00  
276     25                      8               #5 / 8%   Tuesday  07:00:00  
277      1                      0               #6 / 0%   Tuesday  07:00:00  

[278 rows x 11 columns]

Nous pouvons constater que le clustering de New York se réalise de façon cohérente sur cette exemple. Toutefois, je détaillerais mon analyse lors de la visualisation suivante lorsque nous afficherons les clustering par jour de la semaine. 

In [35]:
# Crée un subplot par jour de la semaine
days_of_week = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
figs = sp.make_subplots(rows=int(math.ceil(len(days_of_week)/3)), cols=3, subplot_titles=days_of_week, 
                        specs=[[{'type':'mapbox'}, {'type':'mapbox'}, {'type':'mapbox'}],
                               [{'type':'mapbox'}, {'type':'mapbox'}, {'type':'mapbox'}],
                               [{'type':'mapbox'}, {}, {}]],
                        horizontal_spacing=0.03, vertical_spacing=0.03)

# Paramètres d'affichage par défaut de mapbox
default_mapbox_dict = {'center': {'lat': 40.712559, 'lon': -73.889029},
                       'style': 'carto-positron',
                       'zoom': 8.5
                      }

# Initialise chaque mapbox par jour
for day_index in range(len(days_of_week)):
    figs.update_layout({f'mapbox{day_index+1}': default_mapbox_dict})

# Initialisation du slider
slider_dict = {'active': 0,
               'currentvalue': {'prefix': 'heure='},
               'len': 0.9,
               'pad': {'b': 10, 't': 30},
               'steps': []
              }

# Initialise la liste des traces et des plages horaires
timeframe_index = 0
traces_hour_index = []  # initialise une liste qui associera à chaque trace son index d'heure correspondant pour une utilisation ultérieure dans le masque interactif (slider)


In [36]:
# Rempli les données pour chaque tracé  par heure, jour, cluster

# 1. Boucle sur les trames (heures)
hour_names = ["{:0>2d}:00:00".format(hour_index) for hour_index in range(24)] 
for hour_index in range(24):

    # 2. Boucle sur les subplots (jours de la semaine)
    for day_index, day in enumerate(days_of_week):
        subplot_data = timeframe_summary_list[timeframe_index]
        row_number = day_index // 3 + 1
        col_number = day_index % 3 + 1

        # 3. Boucle sur les traces (clusters)
        for cluster in subplot_data['cluster'].unique():
            cluster_data = subplot_data[subplot_data['cluster'] == cluster]
            if len(cluster_data['cluster / % of demand'].unique()) != 0:
                cluster_name = cluster_data['cluster / % of demand'].unique()[0]
            else: 
                cluster_name = 'aucun cluster trouvé'
            data_dict = {
                'type': 'scattermapbox',
                'text': hour_names[hour_index],
                'hoverinfo': 'all',
                'name': cluster_name,
                'subplot': f'mapbox{day_index+1}',
                'lat': subplot_data['Lat'][subplot_data['cluster'] == cluster],
                'lon': subplot_data['Lon'][subplot_data['cluster'] == cluster],
                'legendgrouptitle': {'text': day},
                'legendgroup': day,
                'showlegend': True,
                'visible': False
            }
            if hour_index == 0:
                data_dict['visible'] = True  # Définit les graphes de la première heure par défaut comme visibles
            figs.add_trace(data_dict)
            traces_hour_index.append(hour_index)
            print(f"graphe créé pour Heure : {hour_index}, Jour : {day}, Cluster : {cluster}")
            clear_output(wait=True)
        timeframe_index += 1


graphe créé pour Heure : 23, Jour : Sunday, Cluster : 2


In [37]:
# Creation du slider
for hour_index in range(24):
    mask = [True if x == hour_index else False for x in traces_hour_index]
    step = {'args': [{'visible': mask},{'showlegend' : mask}],
            'label': hour_names[hour_index],
            'method': 'update'}
    slider_dict['steps'].append(step)
figs.layout.sliders = [slider_dict]

figs.show()

Ces visualisations nous permettent d'identifier 3 éléments importants :

1. Observer l'évolution de la taille d'un cluster au cours de la journée.
2. Comparer la localisation des clusters à une heure donnée pour chaque jour de la semaine.
3. Voir dans la légende la proportion de la demande de la plage horaire que représente chaque cluster.

Toutefois, la demande de la plage horaire ne doit pas être confondue avec la demande moyenne sur toutes les plages horaires. En effet, les clusters affichés ne sont pas vraiment des 'clusters' car ils ne tiennent pas directement compte de la densité de la demande. Cela est crucial dans notre cas, car tous les points sont affichés, même dans les zones à très faible demande.

Pour améliorer cela, nous pourrions filtrer les clusters représentant un pourcentage trop faible de la demande de la plage horaire. Cependant, il serait plus direct et pertinent d'utiliser un modèle DBSCAN puisqu'il se base directement sur le calcul de la densité des points.

#### 8. Modele DBScan

Dans notre approche pour entraîner un modèle de DBSCAN, nous allons inclure l'utilisation de GridSearch pour optimiser le paramètre eps, garantissant ainsi des clusters de haute qualité.

Nous commencerons par prétraiter les données en convertissant les coordonnées géographiques en coordonnées cartésiennes 3D, ce qui simplifie le calcul des distances. Ces coordonnées cartésiennes seront ensuite utilisées comme caractéristiques pour le clustering.

Pour définir les paramètres de DBSCAN, nous fixons min_samples à 3% de la demande moyenne par plage horaire, garantissant que les clusters sont significatifs. En analysant les données, nous avons constaté que la demande peut varier considérablement entre différentes plages horaires. En fixant min_samples à 3% de la demande moyenne, nous nous assurons que chaque cluster identifié représente une proportion non négligeable de la demande totale, ce qui signifie qu'il y a suffisamment de points pour former un cluster dense et pertinent.

Nous effectuerons ensuite une recherche en grille sur une plage de valeurs pour eps (de 0.1 à 1.0) afin de trouver la meilleure valeur qui maximise le score de silhouette. Pour chaque plage horaire, nous trouverons le meilleur eps.

Enfin, nous résumerons les données en calculant la demande pour chaque cluster et le pourcentage de la demande totale qu'il représente, nous permettant ainsi d'obtenir une vue d'ensemble des zones de forte demande et d'optimiser la répartition des chauffeurs.

Cette approche structurée et systématique nous assure d'obtenir des résultats précis et pertinents, en maximisant la qualité des clusters identifiés par DBSCAN.

In [10]:
# Fonction pour trouver le meilleur epsilon avec GridSearch
def find_best_eps(data, eps_range, min_samples, metric):
    best_eps = None
    best_score = -1
    
    for eps in eps_range:
        dbscan = DBSCAN(eps=eps, min_samples=min_samples, metric=metric)
        labels = dbscan.fit_predict(data)
        
        # Ignorer les configurations où DBSCAN a échoué
        if len(set(labels)) <= 1:
            continue
        
        score = silhouette_score(data, labels)
        
        if score > best_score:
            best_eps = eps
            best_score = score
    
    return best_eps, best_score


In [11]:
# Défini les paramètres constants de DBSCAN
metric = 'euclidean'
min_samples = int(0.03 * np.mean([len(timeframe_data) for timeframe_data in timeframe_data_list]))  # définir min_samples comme 3% de la demande moyenne globale par plage horaire
eps_range = np.arange(0.1, 1.0, 0.1)

# Exécute des DBSCAN distincts sur chaque plage horaire avec GridSearch pour eps
print(f"Entraînement d'un DBSCAN sur chacune des {len(timeframe_data_list)} plages horaires avec GridSearch pour eps :")
timeframes_nb = len(timeframe_data_list)
progress_percents_to_display = list(range(10, 100, 10))
indexes_to_display_progress = np.ceil([timeframes_nb * percent / 100 for percent in progress_percents_to_display])

for i in range(timeframes_nb):
    data = timeframe_data_list[i][clustering_features]
    
    for eps in eps_range:
        dbscan = DBSCAN(eps=eps, min_samples=min_samples, metric=metric)
        labels = dbscan.fit_predict(data)
        
        # Ignorer les configurations où DBSCAN a échoué
        if len(set(labels)) <= 1:
            continue
        
        score = silhouette_score(data, labels)
        
        if score > best_score:
            best_eps = eps
            best_score = score

Entraînement d'un DBSCAN sur chacune des 168 plages horaires avec GridSearch pour eps :


In [13]:
# Utilise le meilleur eps trouvé
dbscan = DBSCAN(eps=best_eps, min_samples=min_samples, metric=metric)
dbscan.fit(data)
timeframe_data_list[i]['cluster'] = dbscan.labels_
timeframe_data_list[i] = timeframe_data_list[i].sort_values('cluster')

print("Terminé !")


# Exécute des DBSCAN distincts sur chaque plage horaire
print(f"Entraînement d'un DBSCAN sur chacune des {len(timeframe_data_list)} plages horaires (min_samples = {min_samples}) :")
timeframes_nb = len(timeframe_data_list)
progress_percents_to_display = list(range(10, 100, 10))
indexes_to_display_progress = np.ceil([timeframes_nb * percent / 100 for percent in progress_percents_to_display])

for i in range(timeframes_nb):
    dbscan = DBSCAN(eps=eps, min_samples=min_samples, metric=metric)
    dbscan.fit(timeframe_data_list[i][clustering_features])
    timeframe_data_list[i]['cluster'] = dbscan.labels_
    timeframe_data_list[i] = timeframe_data_list[i].sort_values('cluster')
print("Terminé !")


C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = dbscan.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = dbscan.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer

Terminé !
Entraînement d'un DBSCAN sur chacune des 168 plages horaires (min_samples = 5) :


C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = dbscan.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = dbscan.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexe

Terminé !


C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = dbscan.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  timeframe_data_list[i]['cluster'] = dbscan.labels_
C:\Users\33671\AppData\Local\Temp\ipykernel_4156\3718730703.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexe

In [14]:
# Initialise une liste pour stocker les données de chaque plage horaire
timeframe_summary_list = []

for timeframe_data in timeframe_data_list:
    # Crée un dataframe résumant le nombre de demandes de prise en charge pour chaque cluster dans la plage horaire, et le % de la demande de la plage horaire qu'il représente
    timeframe_demand = len(timeframe_data)
    clusters_size = timeframe_data.groupby(['DayOfWeek/Hour', 'cluster']).count()['Lat'].rename('count').reset_index(drop=False)
    clusters_size['%_of_timeframe_demand'] = (clusters_size['count'] / timeframe_demand * 100).astype(int)
    
    # Fusion des informations pour chaque plage horaire
    timeframe_summary = timeframe_data.merge(clusters_size, on=['DayOfWeek/Hour', 'cluster'])
    
    # Crée une colonne avec le texte à afficher pour chaque cluster dans la plage horaire
    timeframe_summary['cluster / % of demand'] = '#' + timeframe_summary['cluster'].astype(str) + ' / ' + timeframe_summary['%_of_timeframe_demand'].astype(str) + '%'
    
    # Sépare l'identification de la plage horaire en deux (jour de la semaine, heure) pour surveiller l'un dans les sous-graphiques et l'autre dans le curseur de la figure plotly
    timeframe_summary['DayOfWeek'] = timeframe_summary['DayOfWeek/Hour'].str.partition('-')[0]
    timeframe_summary['Hour'] = timeframe_summary['DayOfWeek/Hour'].str.partition('-')[2]
    
    timeframe_summary_list.append(timeframe_summary)

In [17]:
print("Exemple pour une plage horaire donnée (sans masquer les outliers) :")
timeframe_example = timeframe_summary_list[50]
display(timeframe_example)
fig = px.scatter_mapbox(timeframe_example, lat='Lat', lon='Lon', 
                        mapbox_style="carto-positron", 
                        color=timeframe_example['cluster / % of demand'].astype(str), 
                        height=700, zoom=10)
fig.show()

Exemple pour une plage horaire donnée (sans masquer les outliers) :


Lat      Lon    DayOfWeek/Hour            x            y  cluster  \
0    40.8853 -73.9033  Tuesday-07:00:00  1335.450690 -4627.777818       -1   
1    40.8116 -73.9398  Tuesday-07:00:00  1333.985163 -4633.778494       -1   
2    41.0528 -74.0323  Tuesday-07:00:00  1321.668634 -4619.032381       -1   
3    40.7433 -73.8850  Tuesday-07:00:00  1339.793273 -4637.265807       -1   
4    40.6771 -74.0066  Tuesday-07:00:00  1331.271346 -4644.714153       -1   
..       ...      ...               ...          ...          ...      ...   
273  40.7194 -73.9601  Tuesday-07:00:00  1334.193005 -4640.684530        2   
274  40.7185 -73.9523  Tuesday-07:00:00  1334.842802 -4640.565596        2   
275  40.7166 -73.9548  Tuesday-07:00:00  1334.678410 -4640.756284        2   
276  40.7173 -73.9605  Tuesday-07:00:00  1334.202695 -4640.840242        2   
277  40.7238 -73.9458  Tuesday-07:00:00  1335.262926 -4640.044659        2   

     count  %_of_timeframe_demand cluster / % of demand DayOfWeek      Hour  
0       36                     12             #-1 / 12%   Tuesday  07:00:00  
1       36                     12             #-1 / 12%   Tuesday  07:00:00  
2       36                     12             #-1 / 12%   Tuesday  07:00:00  
3       36                     12             #-1 / 12%   Tuesday  07:00:00  
4       36                     12             #-1 / 12%   Tuesday  07:00:00  
..     ...                    ...                   ...       ...       ...  
273      6                      2               #2 / 2%   Tuesday  07:00:00  
274      6                      2               #2 / 2%   Tuesday  07:00:00  
275      6                      2               #2 / 2%   Tuesday  07:00:00  
276      6                      2               #2 / 2%   Tuesday  07:00:00  
277      6                      2               #2 / 2%   Tuesday  07:00:00  

[278 rows x 11 columns]

In [18]:
# Creer un subplot par jour
days_of_week = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
figs = sp.make_subplots(rows = int(math.ceil(len(days_of_week)/3)), cols = 3, subplot_titles = days_of_week, 
                        specs = [[{'type':'mapbox'}, {'type':'mapbox'}, {'type':'mapbox'}],
                                 [{'type':'mapbox'}, {'type':'mapbox'}, {'type':'mapbox'}],
                                 [{'type':'mapbox'}, {}, {}]],
                        horizontal_spacing = 0.03, vertical_spacing = 0.03)

# Set default mapbox display settings
default_mapbox_dict = {'center': {'lat': 40.712559, 'lon': -73.889029},
                       'style': 'carto-positron',
                       'zoom': 8.5
                      }

# Initialize each day mapbox
for day_index in range(len(days_of_week)):
    figs.update_layout({f'mapbox{day_index+1}' : default_mapbox_dict})

# Slider initialization
slider_dict = {'active': 0,
               'currentvalue': {'prefix': 'hour='},
               'len': 0.9,
               'pad': {'b': 10, 't': 30},
               'steps': []
              }

# Initialise les timeframe

timeframe_index = 0
traces_hour_index = [] #initialise une liste qui associera son index d'heure dans le masque interactif (slider)

# Remplir les données pour chaque trace (1 tracé par combinaison différente (heure, jour, cluster)
# 1. boucles sur les heures

hour_names = ["{:0>2d}:00:00".format(hour_index) for hour_index in range(24)] 
for hour_index in range(24):

    # 2. bloucle le subplots (jours)

    for day_index, day in enumerate(days_of_week):
        subplot_data = timeframe_summary_list[timeframe_index]
        hide_outliers_mask = subplot_data['cluster']!=-1 
        subplot_data = subplot_data[hide_outliers_mask] # hide outliers on the maps
        row_number = i//3 + 1
        col_number = i%3 + 1

        # 3. Loop on traces (clusters)

        for cluster in subplot_data['cluster'].unique():
            cluster_data = subplot_data[subplot_data['cluster']==cluster]
            if len(cluster_data['cluster / % of demand'].unique()) != 0:
                cluster_name = cluster_data['cluster / % of demand'].unique()[0]
            else: 
                cluster_name = 'no cluster found'
            data_dict = {
                'type' : 'scattermapbox',
                'text': hour_names[hour_index],
                'hoverinfo': 'all',
                'name': cluster_name,
                'subplot': f'mapbox{day_index+1}',
                'lat' : subplot_data['Lat'][subplot_data['cluster'] == cluster],
                'lon' : subplot_data['Lon'][subplot_data['cluster'] == cluster],
                'legendgrouptitle' : {'text' : day},
                'legendgroup' : day,
                'showlegend' : True,
                'visible' : False
            }
            if hour_index == 0:
                data_dict['visible'] = True # Défini les traces de la première heure par défaut sur visible
            figs.add_trace(data_dict)
            traces_hour_index.append(hour_index)
            print(f"Trace created for Hour : {hour_index}, Day : {day}, Cluster : {cluster}")
            clear_output(wait = True)
        timeframe_index += 1

# Crée les étapes du slider

for hour_index in range(24):
    mask = [True if x == hour_index else False for x in traces_hour_index]
    step = {'args': [{'visible': mask},{'showlegend' : mask}],
            'label': hour_names[hour_index],
            'method': 'update'}
    slider_dict['steps'].append(step)
figs.layout.sliders = [slider_dict]

figs.show()